# Unweighted Average

In [1]:
# Importing the libraries
import numpy as np
import pandas as pd
import sklearn
import matplotlib.pyplot as plt
import sys
import numpy
numpy.set_printoptions(threshold=sys.maxsize)

# Importing the dataset
dataset = pd.read_csv('CVD dataset2.csv')
data=dataset.iloc[:, :].values
X = dataset.iloc[:, :-1].values
y = dataset.iloc[:, 16].values
# X = dataset.iloc[:, [ 0, 1, 2, 5, 10, 11, 13, 15]].values

rows = len(data)    # 3 rows in your example
cols = len(data[0])
print(rows)
print(cols)

560
17


In [2]:
dataNoCvd = data[~(data[:,16] > 0.0)]
dataCvd = data[~(data[:,16] < 1.0)]
rowsNoCvd = len(dataNoCvd)    
rowsCvd = len(dataCvd)
print(rowsNoCvd)
print(rowsCvd)
# print(dataNoCvd)
# print(dataCvd)

519
41


In [3]:
def find_NoCvd_limitsArray(i,DownNoCvd, UpNoCvd, fold_NoCvd_total, fold_NoCvd_residue):
    if i>0 :
        DownNoCvd = UpNoCvd
        UpNoCvd= fold_NoCvd_total+UpNoCvd
    if i < fold_NoCvd_residue :
        UpNoCvd+= 1
#     print("NoCvd limits, Down :",DownNoCvd,"Up ",UpNoCvd)
    return   DownNoCvd, UpNoCvd   
 
def find_Cvd_limitsArray(i,DownCvd, UpCvd, fold_Cvd_total, fold_Cvd_residue,cv):
    if i>0 :
        DownCvd = UpCvd
        UpCvd= fold_Cvd_total+UpCvd
    if i >= cv - fold_Cvd_residue :
         UpCvd+= 1     
#     print("Cvd limits, Down :",DownCvd,"Up ",UpCvd)
    return   DownCvd, UpCvd  

def find_testSubset(DownNoCvd,UpNoCvd,DownCvd,UpCvd):
    temp1=dataNoCvd[DownNoCvd:UpNoCvd,:]
    temp2=dataCvd[DownCvd:UpCvd,:]
    temp3=np.concatenate((temp1, temp2))
#     print(len(temp1),"  ",len(temp2),"  ",len(temp3))
    return temp1, temp2, temp3

def find_trainSubset(DownNoCvd,UpNoCvd,DownCvd,UpCvd):
    temp1 = np.delete(dataNoCvd, slice(DownNoCvd, UpNoCvd), axis=0)
    temp2 = np.delete(dataCvd, slice(DownCvd, UpCvd), axis=0)
    temp3 = np.concatenate((temp1, temp2))
#     print(len(temp1),"  ",len(temp2),"  ",len(temp3))
    return temp1, temp2, temp3

In [4]:
from math import sqrt
 
# calculate the Euclidean distance between two vectors
def euclidean_distance(row1, row2):
    distance = 0.0
    for i in range(len(row1)-1):
        distance += (row1[i] - row2[i])**2
    return sqrt(distance)
 
# Locate the most similar neighbors
def get_neighbors(train, test_row, num_neighbors):
    distances = list()
    j = 0
    for train_row in train:
        dist = euclidean_distance(test_row, train_row)
        distances.append((train_row, dist, j))
        j+=1
    distances.sort(key=lambda tup: tup[1],reverse = True)
    neighbors = list()
    index = list()
    for i in range(num_neighbors):
        neighbors.append(distances[i][0])
        index.append(distances[i][2])
    return neighbors,index

def create_train_test_sets(cv,dataNoCvd,dataCvd):
    test_NoCvd_total = [[],[],[],[],[],[],[],[],[],[]]
    test_total = []
    testSubset_total = [[],[],[],[],[],[],[],[],[],[]]
    train_total = []
    train_total_Cvd = []
    train_total_NoCvd = []
    
    rowsNoCvd = len(dataNoCvd)    
    rowsCvd = len(dataCvd)

    fold_Cvd_total = rowsCvd//cv
    fold_Cvd_residue= rowsCvd%cv
    print("fold_Cvd_total  :",fold_Cvd_total," fold_Cvd_residue  :",fold_Cvd_residue)

    fold_NoCvd_total = rowsNoCvd//cv
    fold_NoCvd_residue= rowsNoCvd%cv
    print("fold_NoCvd_total:",fold_NoCvd_total,"fold_NoCvd_residue:",fold_NoCvd_residue)



    
#     print(dataCvd)
    cvd_temp = dataCvd
    for i in range(rowsCvd//2):
        neib = []
        ind = []
        neib,ind= get_neighbors(cvd_temp,cvd_temp[0],1)
        index = ind[0]
        testSubset_total[i%cv].append(cvd_temp[0].tolist())
        testSubset_total[i%cv].append(cvd_temp[index].tolist())
        cvd_temp = np.delete(cvd_temp, index,0)
        cvd_temp = np.delete(cvd_temp, 0,0)
#         print(len(cvd_temp))
    
#     for i in range(len(cvd_temp)):
#         test_Cvd_total[cv-i-1].append(cvd_temp[0].tolist())
    testSubset_total[9].append(cvd_temp[0].tolist())
    
    print(cvd_temp)    
    
    nocvd_temp = dataNoCvd
    for i in range(rowsNoCvd//2):
        neib = []
        ind = []
        neib,ind= get_neighbors(nocvd_temp,nocvd_temp[0],1)
        index = ind[0]
        testSubset_total[i%cv].append(nocvd_temp[0].tolist())
        testSubset_total[i%cv].append(nocvd_temp[index].tolist())
        nocvd_temp = np.delete(nocvd_temp, index,0)
        nocvd_temp = np.delete(nocvd_temp, 0,0)
#         print(len(nocvd_temp)) 

    testSubset_total[9].append(nocvd_temp[0].tolist())
    
    
    for i in range(cv):
        test = []
        X_test = []
#         X_test = np.array(X_test)
#         print(type(X_test))
        y_test = []
        X_train = []
        y_train = []
        trainSubset_NoCvd = []
        trainSubset_Cvd = []
        s = 0
        test = testSubset_total[i]
        for j in range(len(data)):
#             print(data[j])
#             print(test)
            if data[j].tolist() in test:
                s+=1
                testSubset = data[j]
#                 print(type(X_test))
                X_test_temp = np.delete(testSubset, 16, axis=0)
                X_test.append(X_test_temp.tolist())
#                 X_test.append(np.delete(testSubset, 16, axis=0))
                y_test_temp1 = np.delete(testSubset, slice(0, 16), axis=0)
#                 print(y_test_temp)
                y_test_temp = np.reshape(y_test_temp1, len(y_test_temp1))
#                 print(lala)
                y_test.append(y_test_temp[0])
            else:
                testSubset = data[j]
                if testSubset[16] == 1.0:
                    trainSubset_Cvd.append(testSubset)
                else:
                    trainSubset_NoCvd.append(testSubset)
#                 print(type(testSubset))
                X_train_temp = np.delete(testSubset, 16, axis=0)
#                 print(X_train_temp)
                X_train.append(X_train_temp.tolist())
                
#                 X_test.append(np.delete(testSubset, 16, axis=0))
                y_train_temp1 = np.delete(testSubset, slice(0, 16), axis=0)
#                 print(y_test_temp)
                y_train_temp = np.reshape(y_train_temp1, len(y_train_temp1))
#                 print(lala)
                y_train.append(y_train_temp[0])
    
        X_test = np.array(X_test)
        y_test = np.array(y_test)
        X_train = np.array(X_train)
        y_train = np.array(y_train)
        trainSubset_Cvd = np.array(trainSubset_Cvd)
        trainSubset_NoCvd = np.array(trainSubset_NoCvd)
        
        test_total.append([X_test,y_test])
        train_total.append([X_train,y_train]) 
        train_total_NoCvd.append(trainSubset_NoCvd)
        train_total_Cvd.append(trainSubset_Cvd)
        
#     print(nocvd_temp)
    
    return test_total, train_total, train_total_NoCvd, train_total_Cvd



In [5]:
test_total, train_total, train_total_NoCvd, train_total_Cvd = create_train_test_sets(10,dataNoCvd,dataCvd)
# for i in range(10):
#     print(len(test_total[i][1]))

fold_Cvd_total  : 4  fold_Cvd_residue  : 1
fold_NoCvd_total: 51 fold_NoCvd_residue: 9
[[  1.    66.    23.    25.21   2.     3.     1.     0.     2.     2.
   50.     6.5  140.   240.    84.    50.     1.  ]]


In [6]:
# Chech ratio in each train and test set
def find_ratio(index_list):
    one = 0
    lenght=len(index_list[0])
    for i in range(lenght):
#         print(index_list[1])
        if index_list[1][i] == 1.0 :
            one+= 1
    ratio = one/lenght
    return ratio

for i in range(10):
#     print(len(train_total[i][0]))
#     ratio = find_ratio(train_total[i])
#     print("ratio in train set:", ratio)
    ratio = find_ratio(test_total[i])
    print("ratio in test set:", ratio)

ratio in test set: 0.07142857142857142
ratio in test set: 0.07142857142857142
ratio in test set: 0.07142857142857142
ratio in test set: 0.07142857142857142
ratio in test set: 0.07142857142857142
ratio in test set: 0.07142857142857142
ratio in test set: 0.07142857142857142
ratio in test set: 0.07142857142857142
ratio in test set: 0.07142857142857142
ratio in test set: 0.08928571428571429


In [7]:
# Chech ratio in each train and test set
def find_ratio(index_list):
    one = 0
    lenght=len(index_list[0])
    for i in range(lenght):
#         print(index_list[1])
        if index_list[1][i] == 1.0 :
            one+= 1
    ratio = one/lenght
    return ratio

for i in range(10):
#     print(len(train_total[i][0]))
#     ratio = find_ratio(train_total[i])
#     print("ratio in train set:", ratio)
    ratio = find_ratio(train_total[i])
    print("ratio in test set:", ratio)

ratio in test set: 0.07341269841269842
ratio in test set: 0.07341269841269842
ratio in test set: 0.07341269841269842
ratio in test set: 0.07341269841269842
ratio in test set: 0.07341269841269842
ratio in test set: 0.07341269841269842
ratio in test set: 0.07341269841269842
ratio in test set: 0.07341269841269842
ratio in test set: 0.07341269841269842
ratio in test set: 0.07142857142857142


In [8]:
from xgboost import XGBClassifier


def my_fit(ratio,dataNoCvd,dataCvd,params):   
    Subarray=[]
    models = []
    # yarray
    
    rowsNoCvd = len(dataNoCvd)    
    rowsCvd = len(dataCvd)
#     print("Size of NoCvd cases in train set:",rowsNoCvd)
#     print("Size of Cvd cases in train set  :",rowsCvd)


    numOfSubsamples = rowsNoCvd//(rowsCvd*ratio)
    numOfSubsamples= int(numOfSubsamples)
    SubNoCvd = rowsNoCvd//numOfSubsamples
    residue = rowsNoCvd- SubNoCvd*numOfSubsamples
    
#     print(numOfSubsamples)

    Up = 0


    for i in range(numOfSubsamples):
        
        classifier = XGBClassifier(base_score=0.5, booster='gbtree', colsample_bylevel=params[5],
                  colsample_bynode=1, colsample_bytree=1, gamma=params[4],
                  learning_rate=params[0], max_delta_step=0, max_depth=params[1],
                  min_child_weight=params[3], missing=None, n_estimators=params[2], n_jobs=1,
                  nthread=None, objective='binary:logistic', random_state=0,
                  reg_alpha=0, reg_lambda=params[6], scale_pos_weight=params[7], seed=None,
                  silent=None, subsample=1.0, verbosity=1)
    #     print(i)
    #Creating the training set for each model
        Down = Up
        Up= Up + SubNoCvd
        if i < residue :
            Up+= 1
        
#         print(Down)
#         print(Up)
        
        Sub1=dataNoCvd[Down:Up,:]
        Sub2=np.concatenate((Sub1, dataCvd))
        Subarray.append(Sub2)
#         print("Size of subsample",i+1,":",len(Subarray[i]))
    #Dividing to X and y of the previous traing set    
        X=np.delete(Subarray[i], 16, axis=1)
        y=np.delete(Subarray[i], slice(0, 16), axis=1)
        y=np.reshape(y, len(y))
        
        classifier.fit( X, y)
        models.append(classifier)
    return models     

In [31]:
models = my_fit(2,dataNoCvd,dataCvd)   

TypeError: my_fit() missing 1 required positional argument: 'params'

In [9]:
def predict_unweighted_average(models,X):
    y_pred = []
    y_pred_models = []

    models_size = len(models)
    X_size = len(X)
       
    #βρίσκω και αποθηκευω τα predictions κάθε μοντέλου για το Χ_test όχι όμως με την μορφή (0,1) όπως θα έκανε η
# predict αλλά με μορφή πιθανότητας να έρθει 1 με την predict_proba, δηλαδή τώρα ο πίνακας y_pred_models έχει τις 
# πιθανότητες κάθε περίπτωση του X_test να εμφανίσει Cvd
    for i in range(models_size): 
        y_pred_models.append(models[i].predict_proba(X)[:,1]) 

#Παίρνω τις πιθανότητες κάθε μοντέλου και για κάθε μία περίπτωση του X_test κάνω το average των πιθανοτήτων αυτών
# οπότε βγαίνει μια μέση πιθανότητα για κάθε μία περίπτωση του X_test.
    for j in range(X_size):
        sum = 0
        for i in range(models_size):
            sum = sum + y_pred_models[i][j]
        avr = sum/models_size
        if avr>= 0.5 :         #Όμως επειδή θεωρώ ότι το μοντέλο κάνει classification αν η μέση πιθανότητα 
            y_pred.append(1.)  # είναι μεγαλυτερη από 0.5 τότε θα επιστρέφει 1, δηλαδή ότι έχει cvd, αλλιώς 0
        else:
            y_pred.append(0.)
    return y_pred        
        
     

In [12]:
# https://towardsdatascience.com/train-test-split-and-cross-validation-in-python-80b61beca4b6

from sklearn.metrics import  confusion_matrix,roc_curve, roc_auc_score, accuracy_score
from imxgboost.imbalance_xgb import imbalance_xgboost as imb_xgb
from sklearn.model_selection import StratifiedKFold # import KFold
from sklearn import metrics

def my_cross_val( cv, train_total, test_total, train_total_NoCvd, train_total_Cvd,params):
    accuracy = []
    specificity = []
    sensitivity = []
    auc = []
    
    # print(X)
    for i in range(cv):
#         X_train = train_total[i][0]
#         y_train = train_total[i][1]
        X_test = test_total[i][0]
        y_test = test_total[i][1]
        


        models = my_fit( 2, train_total_NoCvd[i], train_total_Cvd[i],params)


        y_pred = predict_unweighted_average(models,X_test)

        cm = confusion_matrix(y_test, y_pred)
    #     print(cm)

        total1=sum(sum(cm))
        #####from confusion matrix calculate accuracy
        accuracy1=(cm[0,0]+cm[1,1])/total1
    #   print ('Accuracy : ', accuracy1)

        specificity1 = cm[0,0]/(cm[0,0]+cm[0,1])
    #   print('Specificity : ', specificity1 )

        sensitivity1 = cm[1,1]/(cm[1,0]+cm[1,1])
    #   print('Sensitivity : ', sensitivity1)
        
#         y = np.array(y_test)
#         pred = np.array(y_pred)
#         fpr, tpr, thresholds = metrics.roc_curve(y, pred, pos_label=2)
#         auc1 = metrics.auc(fpr, tpr)
        
        auc1 = roc_auc_score(y_test, y_pred)

    
        accuracy.append(accuracy1)
        specificity.append(specificity1)
        sensitivity.append(sensitivity1) 
        auc.append(auc1)
    return accuracy, specificity, sensitivity, auc

In [34]:
params = {
                    "learning_rate"    :[ 0.3],  #0.01-0.2 Makes the model more robust by shrinking the weights on each step
                    "max_depth"        :[2],  #3-10 control over-fitting as higher depth will allow model to learn relations very specific to a particular sample
                    "n_estimators"     :[200],
                     "subsample"       :[1.0],         #0.5-1 small values might lead to under-fitting
                    "gamma"            :[1],            #Makes the algorithm conservative --> No overfitting
                    "colsample_bytree" :[0.75], #0.5-1
                     "reg_lambda"      :[2], #  it should be explored to reduce overfitting.
                    "scale_pos_weight" :[3]
} 

In [45]:
comb = compute_comb(params)
print(comb[0])
accuracy, specificity, sensitivity, auc = my_cross_val( 10, train_total, test_total, train_total_NoCvd, train_total_Cvd,comb[0])

[0.1, 1, 100, 3, 0, 0.5, 1, 1]


In [96]:
from statistics import mean
print(mean(accuracy))
print(mean(specificity))
print(mean(sensitivity))
print(mean(auc))

0.6732142857142858
0.689894419306184
0.47
0.579947209653092


In [13]:
# https://www.geeksforgeeks.org/python-all-possible-permutations-of-n-lists/

def compute_comb(params):
    
    # initializing lists 
    list1 = params.get("learning_rate")
    list2 = params.get("max_depth")
    list3 = params.get("n_estimators") 
    list4 = params.get("min_child_weight")
    list5 = params.get("gamma")    
    list6 = params.get("colsample_bytree")
    list7 = params.get("reg_lambda") 
    list8 = params.get("scale_pos_weight")

#     # printing lists  
#     print ("The original lists are : " + str(list1) +
#                                    " " + str(list2) + 
#                                    " " + str(list3) + 
#                                    " " + str(list4) + 
#                                    " " + str(list5) + 
#                                    " " + str(list6) +
#                                    " " + str(list7) +
#                                    " " + str(list8)) 

    # using list comprehension  
    # to compute all possible permutations 
    res = [[i, j, k, l, m, n, o, p] for i in list1  
                                    for j in list2 
                                    for k in list3 
                                    for l in list4 
                                    for m in list5 
                                    for n in list6 
                                    for o in list7
                                    for p in list8] 

    # printing result 
#     print ("All possible permutations are : " +  str(res))
    return res

In [14]:
class style:
    BOLD = '\033[1m'
    END = '\033[0m'

In [15]:
# https://towardsdatascience.com/train-test-split-and-cross-validation-in-python-80b61beca4b6

from sklearn.metrics import  confusion_matrix,roc_curve, roc_auc_score, accuracy_score
from imxgboost.imbalance_xgb import imbalance_xgboost as imb_xgb
from sklearn.model_selection import StratifiedKFold # import KFold
from statistics import mean

def gridsearch(params):
    max_sens = 0
    max_spes = 0
    max_acc = 0
    best_params = []
    max_params = []
    max_auc = 0
    combs = compute_comb(params)
    print(len(combs))
    for j in range(len(combs)):
        print(j)
        accuracy, specificity, sensitivity, auc = my_cross_val( 10, train_total, test_total, train_total_NoCvd, train_total_Cvd,combs[j])
        if mean(sensitivity)> 0.5 and mean(specificity)>0.6 and mean(accuracy)>0.6 and mean(auc)>0.5:
            print(style.BOLD + "----------------------------------------------------------------"+ style.END)
            print(combs[j])
            print (style.BOLD + 'accuracy    ' + style.END, mean(accuracy))
            print (style.BOLD + 'specificity ' + style.END, mean(specificity))
            print (style.BOLD + 'sensitivity ' + style.END, mean(sensitivity))
            print (style.BOLD + 'auc         ' + style.END, mean(auc))
            print(style.BOLD + "----------------------------------------------------------------"+ style.END)
        else:
            print(combs[j])
            print("accuracy    ",mean(accuracy))
            print("specificity ",mean(specificity))
            print("sensitivity ",mean(sensitivity))
            print("auc         ",mean(auc))
        best_params.append([combs[j],mean(accuracy),mean(specificity),mean(sensitivity),mean(auc)])
        if mean(auc)> max_auc:
            max_sens = mean(sensitivity)
            max_spes = mean(specificity)
            max_acc = mean(accuracy)
            max_auc = mean(auc)
            max_params = combs[j]
    return max_sens, max_params, max_spes, max_acc, max_auc, best_params

# Ratio = 2

In [16]:
# https://www.analyticsvidhya.com/blog/2016/03/complete-guide-parameter-tuning-xgboost-with-codes-python/        
params = {
                    "learning_rate"    :[ 0.1, 0.2, 0.3, 0.4],  #0.01-0.2 Makes the model more robust by shrinking the weights on each step
                    "max_depth"        :[1,2, 3,4],  #3-10 control over-fitting as higher depth will allow model to learn relations very specific to a particular sample
                    "n_estimators"     :[100, 200, 300,400],
                     "min_child_weight":[1,2,3,4],         #0.5-1 small values might lead to under-fitting
                    "gamma"            :[0, 0.5,1],            #Makes the algorithm conservative --> No overfitting
                    "colsample_bytree" :[0.5,0.75, 1.0], #0.5-1
                     "reg_lambda"      :[1, 1.5, 2], #  it should be explored to reduce overfitting.
                    "scale_pos_weight" :[1,2,3,4]
        }

In [17]:
max_sens ,max_params, max_spes, max_acc, max_auc, best_params = gridsearch(params)

27648
0
[0.1, 1, 100, 1, 0, 0.5, 1, 1]
accuracy     0.8410714285714286
specificity  0.8959653092006034
sensitivity  0.15
auc          0.5229826546003017
1
----------------------------------------------------------------
[0.1, 1, 100, 1, 0, 0.5, 1, 2]
accuracy     0.6214285714285714
specificity  0.6280920060331825
sensitivity  0.545
auc          0.5865460030165912
----------------------------------------------------------------
2
[0.1, 1, 100, 1, 0, 0.5, 1, 3]
accuracy     0.4392857142857143
specificity  0.41821266968325793
sensitivity  0.72
auc          0.569106334841629
3
[0.1, 1, 100, 1, 0, 0.5, 1, 4]
accuracy     0.3464285714285714
specificity  0.31018099547511313
sensitivity  0.81
auc          0.5600904977375566
4
[0.1, 1, 100, 1, 0, 0.5, 1.5, 1]
accuracy     0.85
specificity  0.9056184012066365
sensitivity  0.15
auc          0.5278092006033183
5
----------------------------------------------------------------
[0.1, 1, 100, 1, 0, 0.5, 1.5, 2]
accuracy     0.6178571428571429
specifi

[0.1, 1, 100, 1, 0.5, 0.5, 1.5, 4]
accuracy     0.3375
specificity  0.3005656108597285
sensitivity  0.81
auc          0.5552828054298642
44
[0.1, 1, 100, 1, 0.5, 0.5, 2, 1]
accuracy     0.8517857142857143
specificity  0.9075414781297134
sensitivity  0.15
auc          0.5287707390648567
45
----------------------------------------------------------------
[0.1, 1, 100, 1, 0.5, 0.5, 2, 2]
accuracy     0.625
specificity  0.6319381598793363
sensitivity  0.545
auc          0.5884690799396681
----------------------------------------------------------------
46
[0.1, 1, 100, 1, 0.5, 0.5, 2, 3]
accuracy     0.4285714285714286
specificity  0.4065610859728507
sensitivity  0.72
auc          0.5632805429864254
47
[0.1, 1, 100, 1, 0.5, 0.5, 2, 4]
accuracy     0.3267857142857143
specificity  0.289027149321267
sensitivity  0.81
auc          0.5495135746606334
48
[0.1, 1, 100, 1, 0.5, 0.75, 1, 1]
accuracy     0.8428571428571429
specificity  0.8959653092006034
sensitivity  0.175
auc          0.53548265460

[0.1, 1, 100, 1, 1, 0.75, 1, 3]
accuracy     0.43214285714285716
specificity  0.4104072398190045
sensitivity  0.72
auc          0.5652036199095023
87
[0.1, 1, 100, 1, 1, 0.75, 1, 4]
accuracy     0.34464285714285714
specificity  0.31018099547511313
sensitivity  0.79
auc          0.5500904977375566
88
[0.1, 1, 100, 1, 1, 0.75, 1.5, 1]
accuracy     0.85
specificity  0.9056184012066365
sensitivity  0.15
auc          0.5278092006033183
89
----------------------------------------------------------------
[0.1, 1, 100, 1, 1, 0.75, 1.5, 2]
accuracy     0.6178571428571429
specificity  0.6261689291101056
sensitivity  0.52
auc          0.5730844645550528
----------------------------------------------------------------
90
[0.1, 1, 100, 1, 1, 0.75, 1.5, 3]
accuracy     0.43214285714285716
specificity  0.4104072398190045
sensitivity  0.72
auc          0.5652036199095023
91
[0.1, 1, 100, 1, 1, 0.75, 1.5, 4]
accuracy     0.3375
specificity  0.3005656108597285
sensitivity  0.81
auc          0.5552828054

----------------------------------------------------------------
[0.1, 1, 100, 2, 0, 0.75, 2, 2]
accuracy     0.6196428571428572
specificity  0.6280542986425339
sensitivity  0.52
auc          0.574027149321267
----------------------------------------------------------------
130
[0.1, 1, 100, 2, 0, 0.75, 2, 3]
accuracy     0.4232142857142857
specificity  0.40079185520361993
sensitivity  0.715
auc          0.55789592760181
131
[0.1, 1, 100, 2, 0, 0.75, 2, 4]
accuracy     0.3214285714285714
specificity  0.2832202111613876
sensitivity  0.81
auc          0.5466101055806938
132
[0.1, 1, 100, 2, 0, 1.0, 1, 1]
accuracy     0.8553571428571428
specificity  0.9056184012066365
sensitivity  0.225
auc          0.5653092006033182
133
----------------------------------------------------------------
[0.1, 1, 100, 2, 0, 1.0, 1, 2]
accuracy     0.6232142857142857
specificity  0.6319381598793363
sensitivity  0.52
auc          0.5759690799396682
-------------------------------------------------------------

[0.1, 1, 100, 2, 0.5, 1.0, 1, 4]
accuracy     0.3267857142857143
specificity  0.2889894419306184
sensitivity  0.81
auc          0.5494947209653092
172
[0.1, 1, 100, 2, 0.5, 1.0, 1.5, 1]
accuracy     0.8607142857142858
specificity  0.9113876319758673
sensitivity  0.225
auc          0.5681938159879336
173
----------------------------------------------------------------
[0.1, 1, 100, 2, 0.5, 1.0, 1.5, 2]
accuracy     0.6285714285714286
specificity  0.6377073906485671
sensitivity  0.52
auc          0.5788536953242835
----------------------------------------------------------------
174
[0.1, 1, 100, 2, 0.5, 1.0, 1.5, 3]
accuracy     0.42678571428571427
specificity  0.40467571644042233
sensitivity  0.715
auc          0.5598378582202111
175
[0.1, 1, 100, 2, 0.5, 1.0, 1.5, 4]
accuracy     0.325
specificity  0.28706636500754146
sensitivity  0.81
auc          0.5485331825037707
176
[0.1, 1, 100, 2, 0.5, 1.0, 2, 1]
accuracy     0.8553571428571428
specificity  0.9094645550527903
sensitivity  0.175

...

[0.4, 4, 400, 3, 0.5, 0.5, 1, 3]
accuracy     0.6785714285714286
specificity  0.6936651583710407
sensitivity  0.49
auc          0.5918325791855203
27471
----------------------------------------------------------------
[0.4, 4, 400, 3, 0.5, 0.5, 1, 4]
accuracy     0.6464285714285715
specificity  0.6550904977375566
sensitivity  0.54
auc          0.5975452488687782
----------------------------------------------------------------
27472
[0.4, 4, 400, 3, 0.5, 0.5, 1.5, 1]
accuracy     0.7625
specificity  0.7995852187028657
sensitivity  0.3
auc          0.5497926093514329
27473
[0.4, 4, 400, 3, 0.5, 0.5, 1.5, 2]
accuracy     0.6928571428571428
specificity  0.7147812971342383
sensitivity  0.42
auc          0.5673906485671192
27474
----------------------------------------------------------------
[0.4, 4, 400, 3, 0.5, 0.5, 1.5, 3]
accuracy     0.6839285714285714
specificity  0.6975113122171945
sensitivity  0.515
auc          0.6062556561085972
----------------------------------------------------

[0.4, 4, 400, 3, 1, 0.5, 1, 4]
accuracy     0.6464285714285715
specificity  0.6588989441930618
sensitivity  0.49
auc          0.5744494720965309
27508
[0.4, 4, 400, 3, 1, 0.5, 1.5, 1]
accuracy     0.7785714285714286
specificity  0.8168552036199095
sensitivity  0.3
auc          0.5584276018099548
27509
[0.4, 4, 400, 3, 1, 0.5, 1.5, 2]
accuracy     0.6964285714285714
specificity  0.714894419306184
sensitivity  0.465
auc          0.589947209653092
27510
[0.4, 4, 400, 3, 1, 0.5, 1.5, 3]
accuracy     0.6607142857142857
specificity  0.6762443438914028
sensitivity  0.47
auc          0.5731221719457014
27511
----------------------------------------------------------------
[0.4, 4, 400, 3, 1, 0.5, 1.5, 4]
accuracy     0.625
specificity  0.6339743589743589
sensitivity  0.515
auc          0.5744871794871795
----------------------------------------------------------------
27512
[0.4, 4, 400, 3, 1, 0.5, 2, 1]
accuracy     0.7678571428571429
specificity  0.8092006033182504
sensitivity  0.25
auc     

[0.4, 4, 400, 4, 0, 0.5, 1.5, 2]
accuracy     0.7
specificity  0.7168552036199095
sensitivity  0.495
auc          0.6059276018099548
27546
----------------------------------------------------------------
[0.4, 4, 400, 4, 0, 0.5, 1.5, 3]
accuracy     0.6803571428571429
specificity  0.6937028657616893
sensitivity  0.52
auc          0.6068514328808446
----------------------------------------------------------------
27547
[0.4, 4, 400, 4, 0, 0.5, 1.5, 4]
accuracy     0.6625
specificity  0.6762443438914028
sensitivity  0.495
auc          0.5856221719457013
27548
[0.4, 4, 400, 4, 0, 0.5, 2, 1]
accuracy     0.7517857142857143
specificity  0.7841628959276018
sensitivity  0.345
auc          0.5645814479638009
27549
[0.4, 4, 400, 4, 0, 0.5, 2, 2]
accuracy     0.7035714285714285
specificity  0.7225867269984917
sensitivity  0.47
auc          0.5962933634992459
27550
[0.4, 4, 400, 4, 0, 0.5, 2, 3]
accuracy     0.6642857142857143
specificity  0.6801659125188537
sensitivity  0.47
auc          0.57508

----------------------------------------------------------------
[0.4, 4, 400, 4, 0.5, 0.5, 2, 3]
accuracy     0.6446428571428572
specificity  0.6551282051282051
sensitivity  0.515
auc          0.5850641025641026
----------------------------------------------------------------
27587
----------------------------------------------------------------
[0.4, 4, 400, 4, 0.5, 0.5, 2, 4]
accuracy     0.6107142857142857
specificity  0.6145927601809955
sensitivity  0.565
auc          0.5897963800904977
----------------------------------------------------------------
27588
[0.4, 4, 400, 4, 0.5, 0.75, 1, 1]
accuracy     0.7785714285714286
specificity  0.8170437405731523
sensitivity  0.3
auc          0.5585218702865762
27589
[0.4, 4, 400, 4, 0.5, 0.75, 1, 2]
accuracy     0.6910714285714286
specificity  0.7071644042232278
sensitivity  0.49
auc          0.5985822021116138
27590
[0.4, 4, 400, 4, 0.5, 0.75, 1, 3]
accuracy     0.6464285714285715
specificity  0.6588235294117647
sensitivity  0.49
auc      

----------------------------------------------------------------
[0.4, 4, 400, 4, 1, 0.5, 1.5, 4]
accuracy     0.6214285714285714
specificity  0.6262066365007541
sensitivity  0.565
auc          0.595603318250377
----------------------------------------------------------------
27620
[0.4, 4, 400, 4, 1, 0.5, 2, 1]
accuracy     0.7928571428571428
specificity  0.8361990950226245
sensitivity  0.25
auc          0.5430995475113122
27621
[0.4, 4, 400, 4, 1, 0.5, 2, 2]
accuracy     0.6803571428571429
specificity  0.6975867269984917
sensitivity  0.465
auc          0.5812933634992459
27622
----------------------------------------------------------------
[0.4, 4, 400, 4, 1, 0.5, 2, 3]
accuracy     0.6339285714285714
specificity  0.6414781297134238
sensitivity  0.545
auc          0.5932390648567119
----------------------------------------------------------------
27623
----------------------------------------------------------------
[0.4, 4, 400, 4, 1, 0.5, 2, 4]
accuracy     0.6017857142857143
spec

In [18]:
print(max_params)
print(max_acc)
print(max_spes)
print(max_sens)
print(max_auc)

[0.3, 2, 100, 3, 0.5, 1.0, 2, 3]
0.6625
0.6628582202111614
0.665
0.6639291101055806


In [19]:
#Τυπώνονται περιπτώσεις που accuracy>0.6 και specificity>0.6 και sensitivity>0.6 και auc>0.6
s = 0
for i in range(len(best_params)):
    if best_params[i][4] > 0.66 :
        print("parameters :",best_params[i][0])
        print("accuracy :",best_params[i][1])
        print("spes     :",best_params[i][2])
        print("sens     :",best_params[i][3])
        print("auc      :",best_params[i][4])
        print("------------------------------------------------")
        s+=1
print(s)

parameters : [0.2, 2, 400, 1, 0, 0.5, 2, 3]
accuracy : 0.7196428571428571
spes     : 0.7302036199095023
sens     : 0.59
auc      : 0.6601018099547511
------------------------------------------------
parameters : [0.3, 2, 100, 3, 0.5, 1.0, 2, 3]
accuracy : 0.6625
spes     : 0.6628582202111614
sens     : 0.665
auc      : 0.6639291101055806
------------------------------------------------
parameters : [0.3, 2, 200, 3, 0.5, 1.0, 2, 3]
accuracy : 0.6625
spes     : 0.6628582202111614
sens     : 0.665
auc      : 0.6639291101055806
------------------------------------------------
parameters : [0.3, 2, 300, 3, 0.5, 1.0, 2, 3]
accuracy : 0.6625
spes     : 0.6628582202111614
sens     : 0.665
auc      : 0.6639291101055806
------------------------------------------------
parameters : [0.3, 2, 400, 3, 0.5, 1.0, 2, 3]
accuracy : 0.6625
spes     : 0.6628582202111614
sens     : 0.665
auc      : 0.6639291101055806
------------------------------------------------
parameters : [0.4, 3, 300, 1, 0, 0.5, 1.5